In [1]:
from sqlalchemy import create_engine
import pandas as pd
import numpy as np
from binance import Client
import matplotlib.pyplot as plt
import seaborn as sns
import xgboost as xgb
import lightgbm as lgb
from sklearn.ensemble import RandomForestClassifier, RandomForestRegressor
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.model_selection import TimeSeriesSplit
import sys
import ta
import yaml
from data import get_data
sys.path.insert(1, '/home/kenny/algotrading/backtesting')
from backtest import * 
from strategies import *
from config import *
color_pal = sns.color_palette()
plt.style.use('fivethirtyeight')
import warnings
warnings.filterwarnings("ignore")

In [ ]:
url = config.DATABASE_URL_1MINUTE
time_frame = config.INTERVAL_1MINUTE
td_days = 0

In [ ]:
client = Client()
engine = create_engine(url=url)

In [ ]:
# with engine.connect() as connection:
#     query = "SELECT name FROM sqlite_schema WHERE type='table'"
#     symbols = [item[0] for item in connection.execute(text(query)).fetchall()]
#     # for symbol in symbols:
#     #     qry = f"SELECT * FROM '{symbol}' WHERE Open_Time < '{pd.to_datetime('today') - timedelta(days = td_days)}'"
#     #     data = pd.DataFrame(connection.execute(text(qry))).set_index("Open_Time")
#     #     data.index = pd.to_datetime(data.index)
#     symbol = symbols[0]
#     qry = f"SELECT * FROM '{symbol}' WHERE Open_Time < '{pd.to_datetime('today') - timedelta(days = td_days)}'"
#     data = pd.DataFrame(connection.execute(text(qry))).set_index("Open_Time")
#     data.index = pd.to_datetime(data.index)

# connection.close()

# print(symbol)
# data

In [ ]:
# data.plot(style='.',
#         figsize=(15, 5),
#         color=color_pal[0],
#         title='SOLUSDT')
# plt.show()

In [ ]:
# fig, axs = plt.subplots(5, 1, figsize=(15, 15), sharex=True)

# fold = 0
# for train_idx, val_idx in tss.split(df):
#     train = data.iloc[train_idx]
#     test = data.iloc[val_idx]
#     train['Close'].plot(ax=axs[fold],
#                           label='Training Set',
#                           title=f'Data Train/Test Split Fold {fold}')
#     test['Close'].plot(ax=axs[fold],
#                          label='Test Set')
#     axs[fold].axvline(test.index.min(), color='black', ls='--')
#     fold += 1
# plt.show()

In [ ]:
symbol = 'BTCUSDT'
data = get_data(symbol)

In [ ]:
data.head()

In [ ]:
data.describe()

In [ ]:
data.tail()

In [ ]:
def indicators_calc(df):
    for i in range(2, 10, 2):
        df[f'RSI_{i}'] = ta.momentum.rsi(df['Close'], window=i)
        df[f'SMA_{i*10}'] = df['Close'].rolling(i*10).mean()
    # df['MACD'] = ta.trend.macd_diff(df['Close'])
    df.dropna(inplace=True)
    return df

In [ ]:
data = indicators_calc(data)
data.head()

In [ ]:
def create_target(df, period):
    df['Target'] = df['Close'].shift(-period) - df['Close']
    df = df[:-period]
    return df

In [ ]:
data = create_target(data, 1)
data.tail()

In [ ]:
tss = TimeSeriesSplit(n_splits=5, test_size=7*24*60)
data = data.sort_index()

fig, axs = plt.subplots(5, 1, figsize=(15, 15), sharex=True)

fold = 0
for train_idx, val_idx in tss.split(data):
    train = data.iloc[train_idx]
    test = data.iloc[val_idx]
    train['Target'].plot(ax=axs[fold],
                          label='Training Set',
                          title=f'Data Train/Test Split Fold {fold}')
    test['Target'].plot(ax=axs[fold],
                         label='Test Set')
    axs[fold].axvline(test.index.min(), color='black', ls='--')
    fold += 1
plt.show()

In [2]:
FEATURES = ['Open',
    'High',
    'Low',
    'Volume',
    'RSI_2',
    'SMA_20',
    'RSI_4',
    'SMA_40',
    'RSI_6',
    'SMA_60',
    'RSI_8',
    'SMA_80']
TARGET = 'Target'

## Train using CV

In [ ]:
tss = TimeSeriesSplit(n_splits=5, test_size=3*24*60)
data = data.sort_index()

fold = 0
preds = []
scores = []

for train_idx, val_idx in tss.split(data):
    train = data.iloc[train_idx]
    test = data.iloc[val_idx]

    X_train = train[FEATURES]
    y_train = train[TARGET]

    X_test = test[FEATURES]
    y_test = test[TARGET]

    reg = lgb(booster='gbtree',    
                           n_estimators=1000,
                           early_stopping_rounds=50,
                           objective='reg:linear',
                           max_depth=3,
                           learning_rate=0.01)
    reg.fit(X_train, y_train,
            eval_set=[(X_train, y_train), (X_test, y_test)],
            verbose=100)

    y_pred = reg.predict(X_test)
    preds.append(y_pred)
    score = np.sqrt(mean_squared_error(y_test, y_pred))
    scores.append(score)

In [ ]:
print(f'RMSE score across folds {np.mean(scores):0.4f}')
print(f'Fold scores:{scores}')

In [ ]:
reg = xgb.XGBRegressor(booster='gbtree',    
                           n_estimators=1000,
                           early_stopping_rounds=50,
                           objective='reg:linear',
                           max_depth=3,
                           learning_rate=0.01)
reg.fit(data[FEATURES], data[TARGET],
        eval_set=[(X_train, y_train), (X_test, y_test)],
        verbose=100)

In [ ]:
y_pred = reg.predict(data[FEATURES])
score = r2_score(data[TARGET].values, y_pred)
print(score)

In [ ]:
y_pred

In [ ]:
data[TARGET].values

## Testing objective function

In [ ]:
def objective(
        self, trial, param_grid, score_metric, number_of_splits=5, test_size=5 * 24 * 60
    ):

        tss = TimeSeriesSplit(n_splits=number_of_splits, test_size=test_size)
        self.df = self.df.sort_index()
        predictions = []
        scores = []

        for train_idx, val_idx in tss.split(self.df):
            train = self.df.iloc[train_idx]
            test = self.df.iloc[val_idx]

            X_train = train[FEATURES]
            y_train = train[TARGET]

            X_test = test[FEATURES]
            y_test = test[TARGET]

            self.model.fit(
                X_train,
                y_train,
                eval_set=[(X_test, y_test)],
                early_stopping_rounds=100,
            )

            y_pred = self.model.predict(X_test)
            predictions.append(y_pred)
            scores.append(score_metric(y_test, y_pred))

        return np.mean(scores)

## Testing model optimization method

In [3]:
import pandas as pd
from model import *
import warnings
warnings.filterwarnings("ignore")
df = pd.read_csv('data.csv')
df.set_index("Time", inplace=True)
model = Model(df, model_name="LightGBM", task_type="classification")

In [4]:
model.indicators_calc()
model.create_target()
model.optimize('/home/kenny/algotrading/model_training/optimization_results', number_of_trials=15)

  0%|          | 0/4 [00:00<?, ?it/s]

[I 2023-02-20 21:35:54,069] A new study created in memory with name: classification LightGBM with metric - log_loss


[LightGBM] [Warning] early_stopping_round is set=286, early_stopping_rounds=286 will be ignored. Current value: early_stopping_round=286
[LightGBM] [Warning] lambda_l1 is set=35, reg_alpha=0.0 will be ignored. Current value: lambda_l1=35
[LightGBM] [Warning] bagging_fraction is set=0.4, subsample=1.0 will be ignored. Current value: bagging_fraction=0.4
[LightGBM] [Warning] min_gain_to_split is set=2.288486811352044, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=2.288486811352044
[LightGBM] [Warning] lambda_l2 is set=95, reg_lambda=0.0 will be ignored. Current value: lambda_l2=95
[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[1]	valid_0's binary_logloss: 0.693058
[2]	valid_0's binary_logloss: 0.692952
[3]	valid_0's binary_logloss: 0.692952
[4]	valid_0's binary_logloss: 0.692848
[5]

[I 2023-02-20 21:35:57,013] Trial 0 finished with value: 17.478168255939387 and parameters: {'n_estimators': 10000, 'learning_rate': 0.12272051942618255, 'num_leaves': 760, 'max_depth': 10, 'lambda_l1': 35, 'lambda_l2': 95, 'min_gain_to_split': 2.288486811352044, 'bagging_fraction': 0.4, 'bagging_freq': 1, 'feature_fraction': 0.8, 'early_stopping_rounds': 286}. Best is trial 0 with value: 17.478168255939387.


[249]	valid_0's binary_logloss: 0.693217
[250]	valid_0's binary_logloss: 0.693217
[251]	valid_0's binary_logloss: 0.693217
[252]	valid_0's binary_logloss: 0.693217
[253]	valid_0's binary_logloss: 0.69322
[254]	valid_0's binary_logloss: 0.69322
[255]	valid_0's binary_logloss: 0.693254
[256]	valid_0's binary_logloss: 0.693254
[257]	valid_0's binary_logloss: 0.693254
[258]	valid_0's binary_logloss: 0.69321
[259]	valid_0's binary_logloss: 0.69321
[260]	valid_0's binary_logloss: 0.693204
[261]	valid_0's binary_logloss: 0.693204
[262]	valid_0's binary_logloss: 0.693204
[263]	valid_0's binary_logloss: 0.693204
[264]	valid_0's binary_logloss: 0.693204
[265]	valid_0's binary_logloss: 0.693204
[266]	valid_0's binary_logloss: 0.693215
[267]	valid_0's binary_logloss: 0.69323
[268]	valid_0's binary_logloss: 0.69323
[269]	valid_0's binary_logloss: 0.693229
[270]	valid_0's binary_logloss: 0.693229
[271]	valid_0's binary_logloss: 0.693229
[272]	valid_0's binary_logloss: 0.693229
[273]	valid_0's binary

...

[152]	valid_0's binary_logloss: 0.692836
[153]	valid_0's binary_logloss: 0.692836
[154]	valid_0's binary_logloss: 0.692836
[155]	valid_0's binary_logloss: 0.692836
[156]	valid_0's binary_logloss: 0.692836
[157]	valid_0's binary_logloss: 0.692836
[158]	valid_0's binary_logloss: 0.692836
[159]	valid_0's binary_logloss: 0.692836
[160]	valid_0's binary_logloss: 0.692836
[161]	valid_0's binary_logloss: 0.692836
[162]	valid_0's binary_logloss: 0.692836
[163]	valid_0's binary_logloss: 0.692836
[164]	valid_0's binary_logloss: 0.692836
[165]	valid_0's binary_logloss: 0.692836
[166]	valid_0's binary_logloss: 0.692836
[167]	valid_0's binary_logloss: 0.692836
[168]	valid_0's binary_logloss: 0.692836
[169]	valid_0's binary_logloss: 0.692836
[170]	valid_0's binary_logloss: 0.692836
[171]	valid_0's binary_logloss: 0.692836
[172]	valid_0's binary_logloss: 0.692836
[173]	valid_0's binary_logloss: 0.692836
[174]	valid_0's binary_logloss: 0.692834
[175]	valid_0's binary_logloss: 0.692834
[176]	valid_0's 

[I 2023-02-20 21:38:13,127] Trial 13 finished with value: 0.5586912409281358 and parameters: {'n_estimators': 10000, 'learning_rate': 0.08305141605543398, 'num_leaves': 880, 'max_depth': 4, 'lambda_l1': 100, 'lambda_l2': 0, 'min_gain_to_split': 5.026176096721426, 'bagging_fraction': 0.8, 'bagging_freq': 1, 'feature_fraction': 0.30000000000000004, 'early_stopping_rounds': 293}. Best is trial 2 with value: 0.6020238575601271.


[1286]	valid_0's binary_logloss: 0.69267
[1287]	valid_0's binary_logloss: 0.69267
[1288]	valid_0's binary_logloss: 0.69267
[1289]	valid_0's binary_logloss: 0.69267
[1290]	valid_0's binary_logloss: 0.69267
[1291]	valid_0's binary_logloss: 0.69267
[1292]	valid_0's binary_logloss: 0.69267
[1293]	valid_0's binary_logloss: 0.69267
[1294]	valid_0's binary_logloss: 0.69267
[1295]	valid_0's binary_logloss: 0.69267
[1296]	valid_0's binary_logloss: 0.69267
[1297]	valid_0's binary_logloss: 0.69267
[1298]	valid_0's binary_logloss: 0.69267
[1299]	valid_0's binary_logloss: 0.69267
[1300]	valid_0's binary_logloss: 0.69267
[1301]	valid_0's binary_logloss: 0.69267
[1302]	valid_0's binary_logloss: 0.69267
[1303]	valid_0's binary_logloss: 0.69267
[1304]	valid_0's binary_logloss: 0.69267
[1305]	valid_0's binary_logloss: 0.69267
[1306]	valid_0's binary_logloss: 0.69267
[1307]	valid_0's binary_logloss: 0.69267
[1308]	valid_0's binary_logloss: 0.69267
[1309]	valid_0's binary_logloss: 0.69267
[1310]	valid_0's

[I 2023-02-20 21:38:14,164] Trial 14 finished with value: 0.5124038131409097 and parameters: {'n_estimators': 10000, 'learning_rate': 0.12077958744281873, 'num_leaves': 1760, 'max_depth': 5, 'lambda_l1': 25, 'lambda_l2': 70, 'min_gain_to_split': 1.3426991483990003, 'bagging_fraction': 0.9, 'bagging_freq': 1, 'feature_fraction': 0.4, 'early_stopping_rounds': 144}. Best is trial 2 with value: 0.6020238575601271.


[26]	valid_0's binary_logloss: 0.693005
[27]	valid_0's binary_logloss: 0.693068
[28]	valid_0's binary_logloss: 0.693068
[29]	valid_0's binary_logloss: 0.693065
[30]	valid_0's binary_logloss: 0.693065
[31]	valid_0's binary_logloss: 0.693065
[32]	valid_0's binary_logloss: 0.693065
[33]	valid_0's binary_logloss: 0.693072
[34]	valid_0's binary_logloss: 0.693066
[35]	valid_0's binary_logloss: 0.693054
[36]	valid_0's binary_logloss: 0.693055
[37]	valid_0's binary_logloss: 0.693074
[38]	valid_0's binary_logloss: 0.693095
[39]	valid_0's binary_logloss: 0.693121
[40]	valid_0's binary_logloss: 0.693121
[41]	valid_0's binary_logloss: 0.693117
[42]	valid_0's binary_logloss: 0.693119
[43]	valid_0's binary_logloss: 0.693119
[44]	valid_0's binary_logloss: 0.693119
[45]	valid_0's binary_logloss: 0.693119
[46]	valid_0's binary_logloss: 0.693111
[47]	valid_0's binary_logloss: 0.693111
[48]	valid_0's binary_logloss: 0.693121
[49]	valid_0's binary_logloss: 0.693121
[50]	valid_0's binary_logloss: 0.693121


## Load best model LightGBM classification

In [ ]:
best_model = "/home/kenny/algotrading/model_training/optimization_results/res_classification/LightGBM_best_parameters_f1.yaml"
df = pd.read_csv('data.csv')
df.set_index("Time", inplace=True)
import yaml
with open(best_model, "r") as file:
    params = yaml.safe_load(file)

In [ ]:
params

In [ ]:
best_value = params['best_value']
metric = params['metric']
print(f'Best value:{best_value} and metric used {metric}')

In [ ]:
del params['best_value']
del params['metric']
params

In [ ]:
tss = TimeSeriesSplit(n_splits=5, test_size=3*24*60)
df = df.sort_index()
df["Target"] = np.where(df["Target"] > 0, 1, 0)

fold = 0
preds = []
scores = []

for train_idx, val_idx in tss.split(df):
    train = df.iloc[train_idx]
    test = df.iloc[val_idx]

    X_train = train[FEATURES]
    y_train = train[TARGET]

    X_test = test[FEATURES]
    y_test = test[TARGET]

    clf = lgb.LGBMClassifier(**params)
    clf.fit(X_train, y_train,
            eval_set=[(X_test, y_test)],
            verbose=100)

    y_pred = clf.predict(X_test)
    preds.append(y_pred)
    score = f1_score(y_test, y_pred)
    scores.append(score)

In [ ]:
print(f'score across folds {np.mean(scores):0.4f}')
print(f'Fold scores:{scores}')

Как видим все работает нормально проверем качество теперь на полной выборке данных.

In [ ]:
clf = lgb.LGBMClassifier(**params)
clf.fit(df[FEATURES], df[TARGET],
        eval_set=[(X_train, y_train), (X_test, y_test)],
        verbose=100)

In [ ]:
y_pred = clf.predict(df[FEATURES])
score = f1_score(df[TARGET].values, y_pred)
print(score)

In [ ]:
tss = TimeSeriesSplit(n_splits=2, test_size=3*24*60)
fold = 0
preds = []
scores = []

for train_idx, val_idx in tss.split(df):
    train = df.iloc[train_idx]
    test = df.iloc[val_idx]

    X_train = train[FEATURES]
    y_train = train[TARGET]

    X_test = test[FEATURES]
    y_test = test[TARGET]

    clf = lgb.LGBMClassifier(**params)
    clf.fit(X_train, y_train,
            eval_set=[(X_test, y_test)],
            verbose=100)

    y_pred = clf.predict(X_test)
    preds.append(y_pred)
    score = f1_score(y_test, y_pred)
    scores.append(score)

In [ ]:
print(f'score across folds {np.mean(scores):0.4f}')
print(f'Fold scores:{scores}')

In [ ]:
import shap
# Fits the explainer
explainer = shap.Explainer(clf.predict, X_test)
# Calculates the SHAP values - It takes some time
shap_values = explainer(X_test)

In [ ]:
from scipy.special import softmax

def print_feature_importances_shap_values(shap_values, features):
    '''
    Prints the feature importances based on SHAP values in an ordered way
    shap_values -> The SHAP values calculated from a shap.Explainer object
    features -> The name of the features, on the order presented to the explainer
    '''
    # Calculates the feature importance (mean absolute shap value) for each feature
    importances = []
    for i in range(shap_values.values.shape[1]):
        importances.append(np.mean(np.abs(shap_values.values[:, i])))
    # Calculates the normalized version
    importances_norm = softmax(importances)
    # Organize the importances and columns in a dictionary
    feature_importances = {fea: imp for imp, fea in zip(importances, features)}
    feature_importances_norm = {fea: imp for imp, fea in zip(importances_norm, features)}
    # Sorts the dictionary
    feature_importances = {k: v for k, v in sorted(feature_importances.items(), key=lambda item: item[1], reverse = True)}
    feature_importances_norm= {k: v for k, v in sorted(feature_importances_norm.items(), key=lambda item: item[1], reverse = True)}
    # Prints the feature importances
    for k, v in feature_importances.items():
        print(f"{k} -> {v:.4f} (softmax = {feature_importances_norm[k]:.4f})")

In [ ]:
print_feature_importances_shap_values(shap_values, FEATURES)

In [ ]:
shap.plots.bar(shap_values)

In [ ]:
shap.summary_plot(shap_values)
# or 
shap.plots.beeswarm(shap_values)